# Big Data and Automated Content Analysis, Final Project 

# Data gathering

Lukas Pechacek
11954922


In [1]:
import json
import urllib
import pandas as pd
import numpy as np
import nltk
from nltk.corpus import state_union
import requests
from bs4 import BeautifulSoup
import os
import re

import requests
import openpyxl as xls

from urllib.request import urlopen
from lxml.html import parse, fromstring

from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import (
    WebDriverWait)
from selenium.webdriver.support import (
    expected_conditions as EC)
from selenium.webdriver.common.by import By

import time  


import json
import csv
from pprint import pprint
from pandas import json_normalize
import time

import matplotlib.pyplot as plt
import seaborn as sns

import lyricsgenius as genius

Found a list of artists on ranker.com. I will first scrape the data, namely the names of the top 25 artists, from here.

In [2]:
r = requests.get('https://www.ranker.com/crowdranked-list/the-greatest-rappers-of-all-time')
soup = BeautifulSoup(r.text, 'html.parser')
results = soup.find_all('meta', attrs={'itemprop':'name'})

In [3]:
del results[0]

Next, I will scrape the top 25 bands from the same website.

In [4]:
r2 = requests.get('https://www.ranker.com/crowdranked-list/overall-best-hip-hop-crew')
soup2 = BeautifulSoup(r2.text, 'html.parser')

In [5]:
results2 = soup2.find_all('meta', attrs={'itemprop':'name'})
del results2[0]
results2

[<meta content="Wu-Tang Clan" itemprop="name"/>,
 <meta content="Outkast" itemprop="name"/>,
 <meta content="A Tribe Called Quest" itemprop="name"/>,
 <meta content="Mobb Deep" itemprop="name"/>,
 <meta content="N.W.A" itemprop="name"/>,
 <meta content="Run–DMC" itemprop="name"/>,
 <meta content="Eric B. &amp; Rakim" itemprop="name"/>,
 <meta content="Public Enemy" itemprop="name"/>,
 <meta content="Bone Thugs-N-Harmony" itemprop="name"/>,
 <meta content="Beastie Boys" itemprop="name"/>,
 <meta content="The Roots" itemprop="name"/>,
 <meta content="Gang Starr" itemprop="name"/>,
 <meta content="De La Soul" itemprop="name"/>,
 <meta content="Fugees" itemprop="name"/>,
 <meta content="Geto Boys" itemprop="name"/>,
 <meta content="Naughty by Nature" itemprop="name"/>,
 <meta content="Cypress Hill" itemprop="name"/>,
 <meta content="Boogie Down Productions" itemprop="name"/>,
 <meta content="Grandmaster Flash and the Furious Five" itemprop="name"/>,
 <meta content="EPMD" itemprop="name"/>,

In [6]:
artists = results+results2 #adding the two parsed webpages
artists = [meta["content"] for meta in artists] #looping over tags in list to only keep the contents.
print(artists)

['Eminem', 'Tupac', 'The Notorious B.I.G.', 'Kendrick Lamar', 'Nas', 'Dr. Dre', 'Lil Wayne', 'J. Cole', 'Ice Cube', 'Jay-Z', 'Snoop Dogg', 'Kanye West', 'André 3000', '50 Cent', 'Eazy-E', 'DMX', 'Drake', 'Busta Rhymes', 'ASAP Rocky', 'Kid Cudi', 'Ghostface Killah', 'Logic', 'Chance the Rapper', 'Childish Gambino', 'Nate Dogg', 'Wu-Tang Clan', 'Outkast', 'A Tribe Called Quest', 'Mobb Deep', 'N.W.A', 'Run–DMC', 'Eric B. & Rakim', 'Public Enemy', 'Bone Thugs-N-Harmony', 'Beastie Boys', 'The Roots', 'Gang Starr', 'De La Soul', 'Fugees', 'Geto Boys', 'Naughty by Nature', 'Cypress Hill', 'Boogie Down Productions', 'Grandmaster Flash and the Furious Five', 'EPMD', 'The Pharcyde', 'Three 6 Mafia', 'The LOX', 'Tha Dogg Pound', 'Clipse']


In [7]:
artists[1] = '2Pac'
artists[-18] = 'Run–D.M.C.'
artists[-6] = 'Grandmaster Flash & the Furious Five'
artists[-2] = 'Method Man & Redman'
artists[-1] = 'Pete Rock & C.L. Smooth'
artists[18] = 'A$AP Rocky'

In [8]:
#Creating a seperate for artists that do not have up to 90 songs on Genius. These artists all have at least 60 songs. Therefore
#still deemed as sufficient to be included in the analysis.
artists60 = artists[-21], artists[-19], artists[-1]
artists60

('N.W.A', 'Eric B. & Rakim', 'Pete Rock & C.L. Smooth')

In [9]:
print(artists)

['Eminem', '2Pac', 'The Notorious B.I.G.', 'Kendrick Lamar', 'Nas', 'Dr. Dre', 'Lil Wayne', 'J. Cole', 'Ice Cube', 'Jay-Z', 'Snoop Dogg', 'Kanye West', 'André 3000', '50 Cent', 'Eazy-E', 'DMX', 'Drake', 'Busta Rhymes', 'A$AP Rocky', 'Kid Cudi', 'Ghostface Killah', 'Logic', 'Chance the Rapper', 'Childish Gambino', 'Nate Dogg', 'Wu-Tang Clan', 'Outkast', 'A Tribe Called Quest', 'Mobb Deep', 'N.W.A', 'Run–DMC', 'Eric B. & Rakim', 'Run–D.M.C.', 'Bone Thugs-N-Harmony', 'Beastie Boys', 'The Roots', 'Gang Starr', 'De La Soul', 'Fugees', 'Geto Boys', 'Naughty by Nature', 'Cypress Hill', 'Boogie Down Productions', 'Grandmaster Flash and the Furious Five', 'Grandmaster Flash & the Furious Five', 'The Pharcyde', 'Three 6 Mafia', 'The LOX', 'Method Man & Redman', 'Pete Rock & C.L. Smooth']


Next, I will delete artists that have less than 40 songs on Genius.

In [10]:
del artists[-1]#deleting Pete Rock

In [11]:
del artists [-1]#deleting method man and redman

In [12]:
del artists[-1]#the LOX

In [13]:
print(artists)

['Eminem', '2Pac', 'The Notorious B.I.G.', 'Kendrick Lamar', 'Nas', 'Dr. Dre', 'Lil Wayne', 'J. Cole', 'Ice Cube', 'Jay-Z', 'Snoop Dogg', 'Kanye West', 'André 3000', '50 Cent', 'Eazy-E', 'DMX', 'Drake', 'Busta Rhymes', 'A$AP Rocky', 'Kid Cudi', 'Ghostface Killah', 'Logic', 'Chance the Rapper', 'Childish Gambino', 'Nate Dogg', 'Wu-Tang Clan', 'Outkast', 'A Tribe Called Quest', 'Mobb Deep', 'N.W.A', 'Run–DMC', 'Eric B. & Rakim', 'Run–D.M.C.', 'Bone Thugs-N-Harmony', 'Beastie Boys', 'The Roots', 'Gang Starr', 'De La Soul', 'Fugees', 'Geto Boys', 'Naughty by Nature', 'Cypress Hill', 'Boogie Down Productions', 'Grandmaster Flash and the Furious Five', 'Grandmaster Flash & the Furious Five', 'The Pharcyde', 'Three 6 Mafia']


In [14]:
del artists[-3] #deleting Grandmaster Flash & the Furious Five

In [15]:
del artists[12]#deleting andre 3000

In [16]:
del artists[-15] #deleting eric b rakim

In [17]:
del artists[-16] #deleting NWA

In [18]:
del artists [-3] #deleting Grandmaster Flash

In [19]:
del artists [-14]

In [20]:
print(artists)

['Eminem', '2Pac', 'The Notorious B.I.G.', 'Kendrick Lamar', 'Nas', 'Dr. Dre', 'Lil Wayne', 'J. Cole', 'Ice Cube', 'Jay-Z', 'Snoop Dogg', 'Kanye West', '50 Cent', 'Eazy-E', 'DMX', 'Drake', 'Busta Rhymes', 'A$AP Rocky', 'Kid Cudi', 'Ghostface Killah', 'Logic', 'Chance the Rapper', 'Childish Gambino', 'Nate Dogg', 'Wu-Tang Clan', 'Outkast', 'A Tribe Called Quest', 'Mobb Deep', 'Run–D.M.C.', 'Bone Thugs-N-Harmony', 'Beastie Boys', 'The Roots', 'Gang Starr', 'De La Soul', 'Fugees', 'Geto Boys', 'Naughty by Nature', 'Cypress Hill', 'Boogie Down Productions', 'The Pharcyde', 'Three 6 Mafia']


In [21]:
#saving list as text file. 
# open file in write mode
with open(r'artistshiphop.txt', 'w') as fp:
    for item in artists:
        # write each item on a new line
        fp.write("%s\n" % item)
    print('Done')

Done


In [22]:
#saving list as text file
# open file in write mode
with open(r'artistshiphop2.txt', 'w') as fp:
    for item in artists60:
        # write each item on a new line
        fp.write("%s\n" % item)
    print('Done')

Done


https://pynative.com/python-write-list-to-file/ 

In [23]:
artists_list = []

# open file and read the content in a list
with open(r'artistshiphop.txt', 'r') as fp:
    for line in fp:
        # remove linebreak from a current name
        # linebreak is the last character of each line
        x = line[:-1]

        # add current item to the list
        artists_list.append(x)

# display list
print(artists_list)

['Eminem', '2Pac', 'The Notorious B.I.G.', 'Kendrick Lamar', 'Nas', 'Dr. Dre', 'Lil Wayne', 'J. Cole', 'Ice Cube', 'Jay-Z', 'Snoop Dogg', 'Kanye West', '50 Cent', 'Eazy-E', 'DMX', 'Drake', 'Busta Rhymes', 'A$AP Rocky', 'Kid Cudi', 'Ghostface Killah', 'Logic', 'Chance the Rapper', 'Childish Gambino', 'Nate Dogg', 'Wu-Tang Clan', 'Outkast', 'A Tribe Called Quest', 'Mobb Deep', 'Run–D.M.C.', 'Bone Thugs-N-Harmony', 'Beastie Boys', 'The Roots', 'Gang Starr', 'De La Soul', 'Fugees', 'Geto Boys', 'Naughty by Nature', 'Cypress Hill', 'Boogie Down Productions', 'The Pharcyde', 'Three 6 Mafia']


In [24]:
artists60_list = []

# open file and read the content in a list
with open(r'artistshiphop2.txt', 'r') as fp:
    for line in fp:
        # remove linebreak from a current name
        # linebreak is the last character of each line
        x = line[:-1]

        # add current item to the list
        artists60_list.append(x)

# display list
print(artists60_list)

['N.W.A', 'Eric B. & Rakim', 'Pete Rock & C.L. Smooth']


In [25]:
Access_token = 'rn5xRIfu1TMdET-7D_ifSbzd2fUV-TQX_gDhzSykScxwPUUmjJCHbJpUE67Q1ZAH' #Access token of Genius API
Bearer  = '5Iln7M_YnSDZRP34lOzMNh9NL6PiI0pY2r8BSpbCYONVw0w4T_3LcbIjvsS63zva'

In [26]:
#To get the information we want, i.e. the names of the artists we need to also go through all the pages. By following the API 
#guidelines on the website I defined a function that gets this information. I am making 10 requets per page since most pages
#seem to have 10 songs on display by each artist. 

def get_artists(artist_names, page):
    base_url = 'https://api.genius.com'
    headers = {'Authorization': 'Bearer ' + Access_token}
    search_url = base_url + '/search?per_page=10&page=' + str(page)
    data = {'q': artist_names}
    response = requests.get(search_url, data=data, headers=headers)
    return response

The codes above and below were adapted https://medium.com/analytics-vidhya/how-to-scrape-song-lyrics-a-gentle-python-tutorial-5b1d4ab351d2 

In [27]:
# Get artist object from Genius API


# Get Genius.com song url's from artist object
def request_song_url(artist_names, song_cap):
    page = 1
    songs = []
    
    while True:
        response = get_artists(artist_names, page)
        json = response.json()        # Collect up to song_cap song objects from artist
        song_info = []
        for hit in json['response']['hits']:
            if artist_names.lower() in hit['result']['primary_artist']['name'].lower():
                song_info.append(hit)               
    
# Collect song URL's from song objects
        for song in song_info:
            if (len(songs) < song_cap):
                url = song['result']['url']
                songs.append(url)
            
        if (len(songs) == song_cap):
            break
        else:
            page += 1
        
    print('Found {} songs by {}'.format(len(songs), artist_names))
    return songs

In [28]:
#test
print(request_song_url('A Tribe Called Quest', 50)) 

Found 50 songs by A Tribe Called Quest
['https://genius.com/A-tribe-called-quest-electric-relaxation-lyrics', 'https://genius.com/A-tribe-called-quest-we-the-people-lyrics', 'https://genius.com/A-tribe-called-quest-scenario-lyrics', 'https://genius.com/A-tribe-called-quest-can-i-kick-it-lyrics', 'https://genius.com/A-tribe-called-quest-check-the-rhime-lyrics', 'https://genius.com/A-tribe-called-quest-buggin-out-lyrics', 'https://genius.com/A-tribe-called-quest-bonita-applebum-lyrics', 'https://genius.com/A-tribe-called-quest-jazz-weve-got-lyrics', 'https://genius.com/A-tribe-called-quest-the-space-program-lyrics', 'https://genius.com/A-tribe-called-quest-award-tour-lyrics', 'https://genius.com/A-tribe-called-quest-excursions-lyrics', 'https://genius.com/A-tribe-called-quest-conrad-tokyo-lyrics', 'https://genius.com/A-tribe-called-quest-dis-generation-lyrics', 'https://genius.com/A-tribe-called-quest-hot-sex-lyrics', 'https://genius.com/A-tribe-called-quest-the-donald-lyrics', 'https://

In [30]:
ALLSONGS = 90

artistsurl = []
top90songs = []
urls = []


for a in artists_list:
    print(a)
    y = (request_song_url(a, ALLSONGS))#Finding 90 songs for each artist
    top90songs.append(y)
    for v in y:
        artistsurl.append(a)
        urls.append(v)

for s in artists60_list:
    print(s)
    x = (request_song_url(s, 60)) #finding 60 songs for artists with only 60 songs on Genius.
    top90songs.append(x)
    for t in x:
        artistsurl.append(s)
        urls.append(t)
    
print(len(urls), 'urls have been gathered.')


Eminem
Found 90 songs by Eminem
2Pac
Found 90 songs by 2Pac
The Notorious B.I.G.
Found 90 songs by The Notorious B.I.G.
Kendrick Lamar
Found 90 songs by Kendrick Lamar
Nas
Found 90 songs by Nas
Dr. Dre
Found 90 songs by Dr. Dre
Lil Wayne
Found 90 songs by Lil Wayne
J. Cole
Found 90 songs by J. Cole
Ice Cube
Found 90 songs by Ice Cube
Jay-Z
Found 90 songs by Jay-Z
Snoop Dogg
Found 90 songs by Snoop Dogg
Kanye West
Found 90 songs by Kanye West
50 Cent
Found 90 songs by 50 Cent
Eazy-E
Found 90 songs by Eazy-E
DMX
Found 90 songs by DMX
Drake
Found 90 songs by Drake
Busta Rhymes
Found 90 songs by Busta Rhymes
A$AP Rocky
Found 90 songs by A$AP Rocky
Kid Cudi
Found 90 songs by Kid Cudi
Ghostface Killah
Found 90 songs by Ghostface Killah
Logic
Found 90 songs by Logic
Chance the Rapper
Found 90 songs by Chance the Rapper
Childish Gambino
Found 90 songs by Childish Gambino
Nate Dogg
Found 90 songs by Nate Dogg
Wu-Tang Clan
Found 90 songs by Wu-Tang Clan
Outkast
Found 90 songs by Outkast
A Tribe 

In [31]:
len(artistsurl)

3870

In [32]:
len(artists_list), len(artists60_list)

(41, 3)

In [33]:
artists_list.extend(artists60_list) #Rejoining lists in case for later use

In [34]:
len(artists_list)

44

https://stackoverflow.com/questions/63722512/error-while-scraping-website-using-beautifulsoup I kept running into errors while scraping with BeautifulSoup, whilst also trying all possible solutions for a few days. I finally found this code that helped. Apparently the website returned two html versions. I do not claim this code as my own.

In [35]:
lyrics_list = []

for url in urls:
    
    soup = BeautifulSoup(requests.get(url).content, 'html.parser')

    for tag in soup.select('div[class^="Lyrics__Container"], .song_body-lyrics p'):
        
            for i in tag.select('i'):
                i.unwrap()
                tag.smooth()

    t = tag.get_text(strip=True, separator='\n')
    #remove identifiers like chorus, verse, etc
    t = re.sub(r'[\(\[].*?[\)\]]', '', t)  #Some early stage preprocessing
    t = os.linesep.join([s for s in t.splitlines() if s]) #removing empty lines        
            

    if t:
        print(t)
        lyrics_list.append(t)
        

I'm beginnin' to feel like a Rap God, Rap God
All my people from the front to the back nod, back nod
The way I'm racin' around the track, call me NASCAR, NASCAR
Dale Earnhardt of the trailer park, the White Trash God
Kneel before General Zod
This planet's Krypton—no, Asgard, Asgard
So you'll be Thor and I'll be Odin
You rodent, I'm omnipotent
Let off, then I'm reloadin'
Immediately with these bombs I'm totin'
And I should not be woken
I'm the walkin' dead, but I'm just a talkin' head, a zombie floatin'
But I got your mom deep-throatin'
I'm out my Ramen Noodle
We have nothin' in common, poodle
I'm a Doberman, pinch yourself in the arm and pay homage, pupil
It's me, my honesty's brutal
But it's honestly futile if I don't utilize what I do though
For good at least once in a while
So I wanna make sure somewhere in this chicken scratch I scribble and doodle enough rhymes
To maybe try to help get some people through tough times
But I gotta keep a few punchlines
Just in case 'cause even you u

In [36]:
print(len(artistsurl)), print(len(lyrics_list)), print(len(urls))

3870
3784
3870


(None, None, None)

In [37]:
#creating dataframe
a = {'Artist': artistsurl , 'lyrics':lyrics_list , 'URL' : urls}
hiphopDF = pd.DataFrame.from_dict(a, orient='index')
hiphopDF = hiphopDF.transpose()

In [38]:
pd. set_option('display.max_rows', None)

In [39]:
hiphopDF

Artist  \
0                      Eminem   
1                      Eminem   
2                      Eminem   
3                      Eminem   
4                      Eminem   
5                      Eminem   
6                      Eminem   
7                      Eminem   
8                      Eminem   
9                      Eminem   
10                     Eminem   
11                     Eminem   
12                     Eminem   
13                     Eminem   
14                     Eminem   
15                     Eminem   
16                     Eminem   
17                     Eminem   
18                     Eminem   
19                     Eminem   
20                     Eminem   
21                     Eminem   
22                     Eminem   
23                     Eminem   
24                     Eminem   
25                     Eminem   
26                     Eminem   
27                     Eminem   
28                     Eminem   
29                     Eminem   
30                     Eminem   
31                     Eminem   
32                     Eminem   
33                     Eminem   
34                     Eminem   
35                     Eminem   
36                     Eminem   
37                     Eminem   
38                     Eminem   
39                     Eminem   
40                     Eminem   
41                     Eminem   
42                     Eminem   
43                     Eminem   
44                     Eminem   
45                     Eminem   
46                     Eminem   
47                     Eminem   
48                     Eminem   
49                     Eminem   
50                     Eminem   
51                     Eminem   
52                     Eminem   
53                     Eminem   
54                     Eminem   
55                     Eminem   
56                     Eminem   
57                     Eminem   
58                     Eminem   
59                     Eminem   
60                     Eminem   
61                     Eminem   
62                     Eminem   
63                     Eminem   
64                     Eminem   
65                     Eminem   
66                     Eminem   
67                     Eminem   
68                     Eminem   
69                     Eminem   
70                     Eminem   
71                     Eminem   
72                     Eminem   
73                     Eminem   
74                     Eminem   
75                     Eminem   
76                     Eminem   
77                     Eminem   
78                     Eminem   
79                     Eminem   
80                     Eminem   
81                     Eminem   
82                     Eminem   
83                     Eminem   
84                     Eminem   
85                     Eminem   
86                     Eminem   
87                     Eminem   
88                     Eminem   
89                     Eminem   
90                       2Pac   
91                       2Pac   
92                       2Pac   
93                       2Pac   
94                       2Pac   
95                       2Pac   
96                       2Pac   
97                       2Pac   
98                       2Pac   
99                       2Pac   
100                      2Pac   
101                      2Pac   
102                      2Pac   
103                      2Pac   
104                      2Pac   
105                      2Pac   
106                      2Pac   
107                      2Pac   
108                      2Pac   
109                      2Pac   
110                      2Pac   
111                      2Pac   
112                      2Pac   
113                      2Pac   
114                      2Pac   
115                      2Pac   
116                      2Pac   
117                      2Pac   
118                      2Pac   
119                      2Pac   
120                      2Pac 

In [40]:
#saving data to a csv file
hiphopDF.to_csv('hiphopDF.csv',mode='w',encoding='utf-8', index=False)
